Notebook to check how the algorithm develops every 1000 steps
+ with env to make changes

In [1]:
from opt.mc_sim import *
from common.variables import *
from sim.sim_functions import *
import torch
import gym
from gym import spaces
from gym import Env
from gym.spaces import Discrete, Box, MultiDiscrete, Tuple, MultiBinary
from stable_baselines3.common.env_checker import check_env

/usr/local/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
s = SourcingEnv()

In [3]:
class CustomGymEnv(Env):

    def __init__(self, sourcing_env):
            self.SourcingEnv = sourcing_env
            self.counter = 0
    
            # Actions we can take
            self.action_space = MultiDiscrete([INVEN_LIMIT,INVEN_LIMIT])
            
            # Inventory Observation State
            self.observation_space = Box(low=np.array([-30, 0, 0, 0, 0]), high=np.array([30, 30, 30, 1, 1]), shape=(5,), dtype=int)
                                                   
        
    def step(self, action):
                                            
            next_state, event, i, event_probs, supplier_index = self.SourcingEnv.step(action)
            self.counter += 1
            
            if (next_state.s) >=0: 
                reward = -float((H_COST * next_state.s) + np.sum(np.multiply(action, PROCUREMENT_COST_VEC)))
            else: 
                reward = -float((-B_PENALTY* next_state.s) + np.sum(np.multiply(action, PROCUREMENT_COST_VEC)))
            
            info = {}
            
            if self.counter < PERIODS:
                done = False
                
            else:
                done = True
                print([action])  #See decisions it is taking (end of periods only...)
            
            next_state_array = np.array(next_state.get_list_repr())
            return next_state_array, reward, done, info
        
    def reset(self):
            self.SourcingEnv = SourcingEnv()
            return np.array(self.SourcingEnv.current_state.get_list_repr())

In [4]:
s = SourcingEnv()
custom_gym_env = CustomGymEnv(s)

In [5]:
str(custom_gym_env.SourcingEnv.current_state.get_list_repr()), str(custom_gym_env.SourcingEnv.current_state.s)

('[0, 0, 0, 1, 1]', '0')

In [6]:
check_env(custom_gym_env) #warn=True)

[array([ 4, 16])]
[array([22, 25])]


In [7]:
from stable_baselines3 import A2C, DDPG, DQN, PPO, TD3, SAC
import os
from stable_baselines3.common.vec_env import VecFrameStack
from stable_baselines3.common.evaluation import evaluate_policy

# Test

In [8]:
log_path = os.path.join('Test_Manual')
model = PPO("MlpPolicy", custom_gym_env, verbose=1, tensorboard_log=log_path, gamma=0.8)

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


In [9]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_1
[array([17,  6])]
[array([15, 22])]
[array([11, 19])]
[array([15,  0])]
[array([17, 22])]
[array([25, 12])]
[array([29, 11])]
[array([15, 20])]
[array([ 5, 27])]
[array([3, 3])]
[array([28, 27])]
[array([ 0, 23])]
[array([ 8, 28])]
[array([25, 24])]
[array([ 5, 25])]
[array([3, 2])]
[array([18, 19])]
[array([26, 24])]
[array([18,  3])]
[array([19, 15])]
[array([29,  5])]
[array([ 3, 14])]
[array([24, 16])]
[array([12, 20])]
[array([ 7, 28])]
[array([24, 19])]
[array([20, 21])]
[array([24, 14])]
[array([27, 23])]
[array([16, 19])]
[array([29, 28])]
[array([29, 10])]
[array([11,  1])]
[array([9, 7])]
[array([17, 22])]
[array([28,  6])]
[array([ 7, 22])]
[array([11, 27])]
[array([1, 9])]
[array([15, 28])]
[array([25,  1])]
[array([21,  2])]
[array([11,  0])]
[array([24, 13])]
[array([12, 18])]
[array([27, 12])]
[array([14, 13])]
[array([11, 12])]
[array([26, 22])]
[array([12,  2])]
[array([1, 1])]
[array([ 3, 17])]
[array([1, 4])]
[array([ 4, 13])]
[array([ 4,

[array([14, 17])]
[array([24,  2])]
[array([11,  8])]
[array([ 2, 10])]
[array([ 3, 22])]
[array([17, 21])]
[array([21, 17])]
[array([14, 18])]
[array([19, 12])]
[array([7, 0])]
[array([12, 24])]
[array([20,  8])]
[array([24,  0])]
[array([1, 7])]
[array([22, 14])]
[array([ 2, 28])]
[array([11, 13])]
[array([5, 7])]
[array([12, 10])]
[array([7, 0])]
[array([16, 10])]
[array([18, 21])]
[array([ 4, 26])]
[array([16, 13])]
[array([ 8, 18])]
[array([29, 11])]
[array([15, 24])]
[array([24, 27])]
[array([20,  4])]
[array([23, 19])]
[array([23, 17])]
[array([26, 10])]
[array([14, 18])]
[array([2, 2])]
[array([4, 5])]
[array([25,  3])]
[array([4, 5])]
[array([16, 24])]
[array([3, 2])]
[array([24,  8])]
[array([22, 18])]
[array([19, 12])]
[array([24, 29])]
[array([ 6, 15])]
[array([17,  2])]
[array([ 0, 25])]
[array([12, 24])]
[array([ 3, 25])]
[array([10, 27])]
[array([28, 23])]
[array([25, 20])]
[array([16,  1])]
[array([13, 10])]
[array([ 8, 14])]
[array([13,  8])]
[array([ 3, 18])]
[array([

[array([13, 28])]
[array([15, 22])]
[array([ 0, 18])]
[array([26, 28])]
[array([10,  4])]
[array([14,  6])]
[array([3, 2])]
[array([ 8, 16])]
[array([11, 14])]
[array([27, 28])]
[array([20,  9])]
[array([10,  9])]
[array([22,  5])]
[array([29, 20])]
[array([29,  5])]
[array([6, 9])]
[array([19,  0])]
[array([20, 17])]
[array([ 8, 17])]
[array([25, 22])]
[array([ 6, 12])]
[array([29,  6])]
[array([21,  8])]
[array([5, 7])]
[array([16, 28])]
[array([20, 28])]
[array([29,  5])]
[array([ 1, 10])]
[array([14, 17])]
[array([15, 22])]
[array([16, 19])]
[array([28,  9])]
[array([28, 16])]
[array([26, 22])]
[array([24, 26])]
[array([14,  6])]
[array([26, 10])]
[array([ 0, 24])]
[array([21, 10])]
[array([16, 28])]
[array([8, 6])]
[array([10,  1])]
[array([23, 17])]
[array([18, 21])]
[array([28, 16])]
[array([28,  4])]
[array([ 4, 10])]
[array([16, 16])]
[array([19, 12])]
[array([29, 29])]
[array([14, 16])]
[array([8, 6])]
[array([ 4, 20])]
[array([2, 7])]
[array([27, 16])]
[array([28,  5])]
[arr

[array([ 0, 16])]
[array([29,  6])]
[array([15, 13])]
[array([11, 21])]
[array([25, 23])]
[array([15,  3])]
[array([ 3, 18])]
[array([ 5, 14])]
[array([15, 27])]
[array([ 7, 11])]
[array([ 7, 29])]
[array([14, 11])]
[array([18,  6])]
[array([10,  1])]
[array([19, 13])]
[array([ 6, 29])]
[array([28, 27])]
[array([22, 29])]
[array([13, 20])]
[array([28,  0])]
[array([17, 28])]
[array([8, 9])]
[array([ 8, 23])]
[array([5, 8])]
[array([6, 8])]
[array([27,  4])]
[array([ 6, 26])]
[array([17, 12])]
[array([20, 11])]
[array([28, 12])]
[array([ 6, 16])]
[array([ 7, 12])]
[array([ 6, 18])]
[array([ 8, 29])]
[array([ 3, 24])]
[array([18, 14])]
[array([22, 24])]
[array([29, 14])]
[array([29, 23])]
[array([27, 12])]
[array([12,  6])]
[array([28, 21])]
[array([25, 15])]
[array([17,  7])]
[array([28,  7])]
[array([ 9, 17])]
[array([25,  8])]
[array([2, 8])]
[array([22,  0])]
[array([12, 29])]
[array([ 0, 18])]
[array([ 8, 16])]
[array([19, 17])]
[array([ 8, 12])]
[array([14, 28])]
[array([15,  8])]


In [10]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([14,  7]), None)

In [11]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_2
[array([23, 13])]
[array([ 7, 26])]
[array([23, 27])]
[array([ 4, 28])]
[array([19, 29])]
[array([16, 13])]
[array([ 7, 11])]
[array([13, 16])]
[array([21, 26])]
[array([15,  8])]
[array([22, 29])]
[array([18, 25])]
[array([9, 1])]
[array([ 0, 16])]
[array([ 7, 17])]
[array([ 8, 22])]
[array([ 7, 29])]
[array([ 5, 29])]
[array([ 0, 12])]
[array([16,  8])]
[array([25, 11])]
[array([7, 8])]
[array([3, 3])]
[array([15, 17])]
[array([17, 17])]
[array([28, 27])]
[array([22, 10])]
[array([26, 29])]
[array([18, 17])]
[array([ 7, 20])]
[array([19,  4])]
[array([29, 12])]
[array([ 9, 13])]
[array([14, 26])]
[array([5, 2])]
[array([21,  6])]
[array([23, 17])]
[array([21, 23])]
[array([10, 23])]
[array([26, 20])]
[array([28, 23])]
[array([28, 18])]
[array([19, 22])]
[array([ 0, 27])]
[array([28, 29])]
[array([17, 21])]
[array([15, 19])]
[array([20, 11])]
[array([ 0, 26])]
[array([19, 19])]
[array([ 6, 22])]
[array([ 5, 11])]
[array([ 9, 11])]
[array([1, 0])]
[array([ 

[array([11,  9])]
[array([20, 29])]
[array([29, 21])]
[array([ 1, 22])]
[array([ 1, 25])]
[array([25,  9])]
[array([15, 27])]
[array([29, 29])]
[array([ 4, 13])]
[array([10, 11])]
[array([20,  7])]
[array([10, 18])]
[array([24, 22])]
[array([10, 26])]
[array([ 4, 13])]
[array([15,  6])]
[array([ 0, 27])]
[array([19,  8])]
[array([21,  0])]
[array([ 8, 21])]
[array([ 4, 12])]
[array([22, 20])]
[array([ 3, 28])]
[array([26, 11])]
[array([25,  2])]
[array([13,  2])]
[array([27,  4])]
[array([15,  3])]
[array([ 6, 12])]
[array([27,  1])]
[array([3, 5])]
[array([22,  2])]
[array([10, 19])]
[array([ 0, 27])]
[array([4, 7])]
[array([23, 24])]
[array([10,  2])]
[array([26, 25])]
[array([3, 3])]
[array([19, 12])]
[array([29, 20])]
[array([27, 12])]
[array([ 5, 29])]
[array([20,  0])]
[array([13,  5])]
[array([27, 11])]
[array([21, 28])]
[array([26, 21])]
[array([27, 28])]
[array([ 2, 16])]
[array([21,  6])]
[array([20, 16])]
[array([3, 7])]
[array([14, 11])]
[array([13,  3])]
[array([20, 17])]


[array([27, 25])]
[array([27, 20])]
[array([24,  3])]
[array([10, 27])]
[array([17, 16])]
[array([4, 4])]
[array([ 6, 20])]
[array([ 3, 27])]
[array([18, 14])]
[array([ 4, 13])]
[array([ 5, 12])]
[array([18,  9])]
[array([ 4, 19])]
[array([ 2, 14])]
[array([14, 22])]
[array([19, 11])]
[array([28, 17])]
[array([ 1, 25])]
[array([21,  6])]
[array([17,  0])]
[array([ 9, 20])]
[array([18, 14])]
[array([13,  7])]
[array([4, 6])]
[array([22, 18])]
[array([8, 1])]
[array([18, 17])]
[array([13, 17])]
[array([ 3, 28])]
[array([9, 1])]
[array([1, 4])]
[array([10,  6])]
[array([12, 16])]
[array([16, 10])]
[array([28,  5])]
[array([1, 9])]
[array([ 2, 16])]
[array([ 7, 14])]
[array([ 1, 22])]
[array([16, 19])]
[array([5, 6])]
[array([2, 1])]
[array([27,  2])]
[array([10,  4])]
[array([10,  9])]
[array([2, 5])]
[array([ 9, 18])]
[array([21, 27])]
[array([16,  2])]
[array([8, 8])]
[array([ 8, 13])]
[array([14, 13])]
[array([6, 3])]
[array([22, 23])]
[array([17, 13])]
[array([1, 8])]
[array([4, 3])]


[array([ 4, 21])]
[array([22, 17])]
[array([25, 15])]
[array([ 9, 12])]
[array([29, 15])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -680     |
| time/              |          |
|    fps             | 1116     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [12]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([17, 10]), None)

In [13]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_3
[array([ 3, 26])]
[array([ 4, 18])]
[array([11,  4])]
[array([21,  1])]
[array([1, 9])]
[array([18,  0])]
[array([19, 15])]
[array([19,  8])]
[array([21,  4])]
[array([ 5, 10])]
[array([19, 25])]
[array([ 9, 21])]
[array([ 4, 24])]
[array([4, 5])]
[array([20, 18])]
[array([20,  7])]
[array([17, 24])]
[array([9, 8])]
[array([ 2, 12])]
[array([11,  5])]
[array([ 1, 16])]
[array([ 1, 16])]
[array([13,  2])]
[array([23, 13])]
[array([0, 8])]
[array([0, 5])]
[array([27,  9])]
[array([13,  8])]
[array([0, 9])]
[array([20,  8])]
[array([12, 19])]
[array([12, 17])]
[array([13,  6])]
[array([21, 19])]
[array([ 0, 17])]
[array([15, 22])]
[array([4, 2])]
[array([26, 20])]
[array([29,  7])]
[array([23, 27])]
[array([ 3, 23])]
[array([ 6, 24])]
[array([ 6, 12])]
[array([21,  2])]
[array([ 8, 23])]
[array([ 4, 13])]
[array([ 7, 23])]
[array([ 4, 17])]
[array([ 1, 22])]
[array([20, 22])]
[array([20, 13])]
[array([1, 1])]
[array([13, 21])]
[array([7, 4])]
[array([6, 8])]
[

[array([10, 29])]
[array([26, 23])]
[array([23, 25])]
[array([ 9, 25])]
[array([ 8, 14])]
[array([ 8, 18])]
[array([18,  6])]
[array([23, 25])]
[array([23, 14])]
[array([ 1, 10])]
[array([21, 22])]
[array([ 4, 11])]
[array([20, 21])]
[array([26, 27])]
[array([4, 6])]
[array([0, 0])]
[array([ 5, 21])]
[array([15, 11])]
[array([ 0, 28])]
[array([15, 24])]
[array([4, 4])]
[array([21, 28])]
[array([14,  3])]
[array([28, 27])]
[array([21,  9])]
[array([28, 16])]
[array([15, 24])]
[array([ 4, 10])]
[array([14,  3])]
[array([27, 18])]
[array([9, 6])]
[array([2, 0])]
[array([ 5, 28])]
[array([11, 25])]
[array([ 7, 15])]
[array([6, 2])]
[array([ 5, 16])]
[array([9, 1])]
[array([ 4, 13])]
[array([24,  6])]
[array([1, 3])]
[array([ 1, 27])]
[array([ 0, 10])]
[array([11, 21])]
[array([4, 3])]
[array([ 2, 28])]
[array([18,  3])]
[array([24, 12])]
[array([ 1, 15])]
[array([2, 6])]
[array([ 4, 25])]
[array([ 0, 20])]
[array([ 7, 12])]
[array([21, 23])]
[array([7, 3])]
[array([0, 2])]
[array([20,  8])

[array([19, 11])]
[array([29, 15])]
[array([21,  9])]
[array([9, 2])]
[array([ 1, 13])]
[array([18, 25])]
[array([ 3, 12])]
[array([23, 27])]
[array([7, 3])]
[array([ 6, 20])]
[array([6, 0])]
[array([16,  3])]
[array([23,  2])]
[array([ 3, 28])]
[array([ 5, 29])]
[array([26, 22])]
[array([ 7, 22])]
[array([26, 17])]
[array([ 9, 14])]
[array([20, 21])]
[array([20, 17])]
[array([6, 5])]
[array([8, 8])]
[array([ 2, 11])]
[array([18, 23])]
[array([23, 16])]
[array([ 2, 13])]
[array([22,  8])]
[array([4, 8])]
[array([14, 14])]
[array([11, 20])]
[array([24,  8])]
[array([19, 20])]
[array([19,  3])]
[array([ 9, 10])]
[array([27, 14])]
[array([17, 18])]
[array([10, 13])]
[array([26, 28])]
[array([19, 20])]
[array([26,  2])]
[array([18,  4])]
[array([9, 7])]
[array([ 9, 26])]
[array([20, 21])]
[array([ 9, 16])]
[array([ 3, 26])]
[array([ 6, 24])]
[array([6, 4])]
[array([26,  2])]
[array([18,  7])]
[array([25, 14])]
[array([14, 28])]
[array([ 8, 25])]
[array([ 1, 21])]
[array([19, 13])]
[array([

In [14]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([28, 14]), None)

In [15]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_4
[array([ 7, 13])]
[array([18, 11])]
[array([ 8, 15])]
[array([28, 11])]
[array([ 0, 26])]
[array([ 3, 24])]
[array([ 4, 26])]
[array([18, 12])]
[array([ 0, 25])]
[array([ 8, 10])]
[array([28, 21])]
[array([1, 6])]
[array([12,  7])]
[array([3, 9])]
[array([0, 3])]
[array([ 2, 14])]
[array([ 6, 25])]
[array([ 9, 27])]
[array([0, 7])]
[array([ 4, 12])]
[array([13, 20])]
[array([13,  6])]
[array([ 5, 23])]
[array([ 2, 27])]
[array([15,  0])]
[array([24, 21])]
[array([ 5, 22])]
[array([24, 12])]
[array([26, 17])]
[array([ 6, 22])]
[array([5, 3])]
[array([18, 28])]
[array([10, 11])]
[array([3, 7])]
[array([6, 2])]
[array([20,  3])]
[array([ 8, 25])]
[array([ 3, 24])]
[array([ 9, 26])]
[array([1, 6])]
[array([ 8, 19])]
[array([10, 15])]
[array([2, 4])]
[array([ 9, 15])]
[array([12, 19])]
[array([16,  1])]
[array([17, 15])]
[array([ 2, 22])]
[array([2, 2])]
[array([19, 19])]
[array([15, 14])]
[array([4, 8])]
[array([2, 3])]
[array([12, 22])]
[array([ 5, 11])]
[arra

[array([25, 10])]
[array([26,  3])]
[array([ 8, 18])]
[array([23, 16])]
[array([12,  7])]
[array([13, 21])]
[array([11, 21])]
[array([6, 2])]
[array([15,  3])]
[array([26, 20])]
[array([6, 7])]
[array([ 2, 17])]
[array([11, 24])]
[array([11,  3])]
[array([ 7, 17])]
[array([12,  2])]
[array([ 1, 27])]
[array([1, 5])]
[array([ 3, 15])]
[array([23, 25])]
[array([ 7, 23])]
[array([ 6, 15])]
[array([1, 5])]
[array([19, 15])]
[array([ 0, 10])]
[array([ 7, 15])]
[array([ 4, 13])]
[array([ 9, 23])]
[array([6, 2])]
[array([2, 3])]
[array([10, 27])]
[array([ 1, 10])]
[array([17, 20])]
[array([12, 15])]
[array([0, 0])]
[array([6, 3])]
[array([28,  6])]
[array([8, 0])]
[array([22, 27])]
[array([17,  5])]
[array([5, 4])]
[array([0, 7])]
[array([18, 28])]
[array([ 2, 24])]
[array([ 6, 15])]
[array([ 2, 20])]
[array([ 9, 29])]
[array([6, 7])]
[array([6, 9])]
[array([7, 3])]
[array([28, 25])]
[array([7, 1])]
[array([15, 28])]
[array([26,  3])]
[array([7, 5])]
[array([17,  5])]
[array([15,  7])]
[array

[array([ 9, 25])]
[array([27, 19])]
[array([1, 6])]
[array([ 0, 15])]
[array([25,  7])]
[array([ 1, 12])]
[array([7, 0])]
[array([ 6, 10])]
[array([4, 7])]
[array([20,  0])]
[array([20, 25])]
[array([ 5, 12])]
[array([15,  2])]
[array([ 2, 15])]
[array([14,  7])]
[array([10, 23])]
[array([19,  3])]
[array([11,  6])]
[array([23, 22])]
[array([3, 0])]
[array([ 4, 15])]
[array([13, 19])]
[array([ 7, 28])]
[array([25, 15])]
[array([13, 28])]
[array([10,  9])]
[array([12, 17])]
[array([ 9, 19])]
[array([7, 4])]
[array([ 0, 20])]
[array([ 7, 17])]
[array([ 3, 28])]
[array([14, 25])]
[array([4, 4])]
[array([24, 28])]
[array([ 0, 28])]
[array([23, 28])]
[array([3, 6])]
[array([16, 22])]
[array([4, 9])]
[array([ 4, 15])]
[array([6, 3])]
[array([ 8, 27])]
[array([ 9, 22])]
[array([21, 20])]
[array([ 1, 25])]
[array([ 5, 10])]
[array([21,  2])]
[array([20, 13])]
[array([11, 19])]
[array([ 8, 25])]
[array([25, 26])]
[array([4, 3])]
[array([3, 6])]
[array([19,  2])]
[array([ 4, 14])]
[array([17,  8

In [16]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([ 0, 17]), None)

In [17]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_5
[array([ 2, 16])]
[array([ 6, 20])]
[array([20, 14])]
[array([ 1, 28])]
[array([17, 15])]
[array([21,  9])]
[array([ 7, 28])]
[array([ 1, 29])]
[array([ 2, 19])]
[array([10, 26])]
[array([14,  6])]
[array([ 4, 22])]
[array([12,  6])]
[array([0, 8])]
[array([0, 6])]
[array([ 5, 20])]
[array([18, 13])]
[array([ 8, 24])]
[array([22, 24])]
[array([3, 7])]
[array([ 0, 19])]
[array([27, 10])]
[array([12, 29])]
[array([2, 3])]
[array([ 8, 22])]
[array([10,  9])]
[array([11, 24])]
[array([7, 6])]
[array([ 5, 29])]
[array([24,  6])]
[array([ 2, 25])]
[array([2, 6])]
[array([1, 6])]
[array([22,  0])]
[array([7, 2])]
[array([ 3, 19])]
[array([ 0, 24])]
[array([22, 15])]
[array([14, 26])]
[array([ 7, 22])]
[array([ 5, 21])]
[array([24, 29])]
[array([5, 0])]
[array([29, 29])]
[array([0, 1])]
[array([ 3, 27])]
[array([0, 2])]
[array([3, 7])]
[array([23,  5])]
[array([11, 15])]
[array([23, 21])]
[array([24, 10])]
[array([28, 28])]
[array([7, 5])]
[array([10, 25])]
[array(

[array([20, 11])]
[array([20, 28])]
[array([ 3, 22])]
[array([23, 18])]
[array([5, 0])]
[array([3, 0])]
[array([2, 3])]
[array([3, 3])]
[array([4, 0])]
[array([22, 17])]
[array([ 4, 23])]
[array([23, 24])]
[array([10, 18])]
[array([11,  7])]
[array([ 9, 13])]
[array([ 6, 29])]
[array([ 2, 14])]
[array([11,  5])]
[array([16,  9])]
[array([ 0, 25])]
[array([ 2, 25])]
[array([ 9, 27])]
[array([ 6, 26])]
[array([ 9, 15])]
[array([10, 11])]
[array([19, 26])]
[array([17, 26])]
[array([ 0, 29])]
[array([13, 26])]
[array([9, 0])]
[array([20, 25])]
[array([13, 26])]
[array([ 4, 27])]
[array([ 6, 28])]
[array([8, 2])]
[array([17,  4])]
[array([ 2, 28])]
[array([25,  0])]
[array([ 4, 19])]
[array([ 9, 12])]
[array([ 6, 22])]
[array([ 5, 10])]
[array([ 7, 19])]
[array([ 9, 15])]
[array([4, 9])]
[array([17,  6])]
[array([ 6, 10])]
[array([ 7, 28])]
[array([24, 19])]
[array([28, 17])]
[array([3, 9])]
[array([ 4, 27])]
[array([ 9, 13])]
[array([ 8, 28])]
[array([ 3, 10])]
[array([ 7, 28])]
[array([24

[array([6, 3])]
[array([3, 5])]
[array([ 1, 17])]
[array([ 5, 17])]
[array([11,  2])]
[array([ 4, 15])]
[array([ 9, 15])]
[array([14, 15])]
[array([ 1, 17])]
[array([15, 21])]
[array([26,  0])]
[array([13, 18])]
[array([ 3, 21])]
[array([12, 11])]
[array([23,  1])]
[array([ 3, 12])]
[array([29, 25])]
[array([ 6, 10])]
[array([ 2, 12])]
[array([15,  7])]
[array([0, 1])]
[array([9, 8])]
[array([13, 18])]
[array([7, 2])]
[array([21, 27])]
[array([17, 29])]
[array([ 5, 16])]
[array([5, 1])]
[array([16,  0])]
[array([ 7, 26])]
[array([19,  1])]
[array([ 7, 18])]
[array([ 7, 14])]
[array([ 5, 25])]
[array([11, 14])]
[array([5, 1])]
[array([16, 18])]
[array([ 3, 14])]
[array([ 2, 15])]
[array([ 0, 12])]
[array([ 4, 29])]
[array([ 7, 11])]
[array([20, 10])]
[array([ 7, 29])]
[array([5, 3])]
[array([ 7, 12])]
[array([25, 24])]
[array([ 8, 15])]
[array([ 1, 29])]
[array([27,  2])]
[array([ 7, 25])]
[array([ 0, 16])]
[array([ 5, 22])]
[array([3, 5])]
[array([ 7, 10])]
[array([4, 5])]
[array([4, 7

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -495     |
| time/              |          |
|    fps             | 1121     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [18]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([25, 12]), None)

In [19]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_6
[array([17, 15])]
[array([ 5, 19])]
[array([ 5, 10])]
[array([ 8, 28])]
[array([5, 5])]
[array([ 6, 15])]
[array([19, 11])]
[array([5, 2])]
[array([0, 1])]
[array([23,  5])]
[array([ 2, 21])]
[array([21, 15])]
[array([ 1, 29])]
[array([9, 7])]
[array([ 5, 21])]
[array([ 4, 11])]
[array([ 0, 26])]
[array([ 1, 13])]
[array([2, 1])]
[array([ 9, 24])]
[array([ 3, 10])]
[array([ 5, 19])]
[array([19,  9])]
[array([ 9, 28])]
[array([8, 8])]
[array([ 0, 18])]
[array([1, 8])]
[array([2, 2])]
[array([ 4, 22])]
[array([0, 8])]
[array([25, 14])]
[array([12, 13])]
[array([21,  8])]
[array([2, 8])]
[array([ 0, 24])]
[array([24,  6])]
[array([ 2, 23])]
[array([14, 26])]
[array([6, 2])]
[array([3, 9])]
[array([ 6, 22])]
[array([ 0, 15])]
[array([ 6, 23])]
[array([ 7, 29])]
[array([14,  6])]
[array([ 4, 18])]
[array([ 1, 14])]
[array([ 4, 15])]
[array([ 0, 10])]
[array([3, 8])]
[array([ 6, 22])]
[array([ 1, 19])]
[array([1, 1])]
[array([ 9, 18])]
[array([15, 19])]
[array([ 

[array([ 7, 11])]
[array([21, 25])]
[array([ 6, 14])]
[array([ 8, 20])]
[array([ 7, 29])]
[array([ 0, 20])]
[array([23,  5])]
[array([23, 11])]
[array([0, 9])]
[array([6, 6])]
[array([12, 22])]
[array([10, 22])]
[array([ 3, 27])]
[array([16,  8])]
[array([1, 3])]
[array([4, 0])]
[array([ 4, 23])]
[array([15, 24])]
[array([ 0, 29])]
[array([1, 0])]
[array([5, 1])]
[array([ 0, 15])]
[array([1, 9])]
[array([ 6, 16])]
[array([ 9, 14])]
[array([ 4, 24])]
[array([ 2, 10])]
[array([ 3, 10])]
[array([ 5, 19])]
[array([ 1, 12])]
[array([ 9, 21])]
[array([5, 5])]
[array([1, 9])]
[array([ 4, 19])]
[array([25, 15])]
[array([8, 4])]
[array([10, 17])]
[array([ 5, 11])]
[array([ 1, 28])]
[array([ 0, 26])]
[array([13, 27])]
[array([ 2, 18])]
[array([ 6, 28])]
[array([9, 4])]
[array([28, 28])]
[array([ 3, 15])]
[array([ 8, 17])]
[array([6, 9])]
[array([14, 10])]
[array([17, 26])]
[array([ 6, 17])]
[array([9, 5])]
[array([5, 2])]
[array([0, 6])]
[array([2, 8])]
[array([4, 9])]
[array([2, 0])]
[array([18

[array([ 6, 18])]
[array([8, 0])]
[array([14, 24])]
[array([20,  5])]
[array([ 1, 10])]
[array([0, 7])]
[array([2, 0])]
[array([25, 29])]
[array([ 3, 16])]
[array([3, 3])]
[array([8, 1])]
[array([ 6, 22])]
[array([29, 11])]
[array([ 4, 28])]
[array([ 6, 16])]
[array([1, 7])]
[array([4, 9])]
[array([10,  3])]
[array([ 6, 12])]
[array([ 1, 17])]
[array([3, 4])]
[array([ 6, 24])]
[array([21, 18])]
[array([23, 23])]
[array([8, 8])]
[array([10,  9])]
[array([5, 7])]
[array([ 0, 13])]
[array([1, 1])]
[array([8, 4])]
[array([10,  1])]
[array([10,  1])]
[array([ 4, 19])]
[array([8, 9])]
[array([3, 9])]
[array([0, 8])]
[array([17, 22])]
[array([ 9, 23])]
[array([4, 9])]
[array([5, 2])]
[array([ 0, 11])]
[array([3, 9])]
[array([1, 9])]
[array([ 2, 25])]
[array([24,  0])]
[array([7, 1])]
[array([ 4, 12])]
[array([6, 9])]
[array([ 2, 12])]
[array([14,  3])]
[array([ 3, 16])]
[array([5, 2])]
[array([ 6, 14])]
[array([5, 1])]
[array([ 2, 23])]
[array([ 3, 11])]
[array([24, 26])]
[array([0, 8])]
[arr

In [20]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([ 6, 14]), None)

In [21]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_7
[array([21, 29])]
[array([ 1, 21])]
[array([ 5, 21])]
[array([ 2, 27])]
[array([4, 8])]
[array([18, 15])]
[array([ 6, 13])]
[array([ 2, 23])]
[array([5, 7])]
[array([1, 5])]
[array([17,  1])]
[array([ 3, 13])]
[array([5, 7])]
[array([ 3, 12])]
[array([13, 24])]
[array([ 4, 17])]
[array([ 3, 19])]
[array([ 1, 19])]
[array([6, 1])]
[array([ 0, 14])]
[array([ 0, 22])]
[array([0, 3])]
[array([ 5, 16])]
[array([0, 3])]
[array([0, 5])]
[array([12,  1])]
[array([1, 6])]
[array([23,  1])]
[array([1, 7])]
[array([ 7, 29])]
[array([ 9, 19])]
[array([ 7, 24])]
[array([1, 9])]
[array([ 2, 21])]
[array([16, 11])]
[array([1, 8])]
[array([ 5, 10])]
[array([1, 8])]
[array([ 7, 14])]
[array([4, 9])]
[array([ 2, 11])]
[array([10, 11])]
[array([3, 6])]
[array([10,  0])]
[array([0, 1])]
[array([22, 14])]
[array([ 4, 16])]
[array([10, 17])]
[array([13,  7])]
[array([12,  2])]
[array([11, 27])]
[array([12,  1])]
[array([3, 1])]
[array([ 8, 23])]
[array([ 2, 29])]
[array([ 3, 18]

[array([ 2, 25])]
[array([ 0, 28])]
[array([3, 2])]
[array([3, 0])]
[array([1, 3])]
[array([ 3, 14])]
[array([ 6, 23])]
[array([ 2, 23])]
[array([ 1, 15])]
[array([ 1, 25])]
[array([ 7, 21])]
[array([ 8, 11])]
[array([6, 8])]
[array([ 0, 27])]
[array([ 4, 18])]
[array([2, 3])]
[array([ 0, 18])]
[array([ 6, 11])]
[array([5, 0])]
[array([27, 13])]
[array([ 4, 16])]
[array([ 2, 12])]
[array([4, 6])]
[array([5, 2])]
[array([ 0, 19])]
[array([5, 3])]
[array([14,  4])]
[array([7, 4])]
[array([12, 17])]
[array([2, 1])]
[array([ 7, 25])]
[array([5, 0])]
[array([ 5, 28])]
[array([ 2, 19])]
[array([ 0, 24])]
[array([0, 9])]
[array([ 0, 21])]
[array([4, 0])]
[array([6, 3])]
[array([ 3, 10])]
[array([ 0, 21])]
[array([ 9, 14])]
[array([16,  2])]
[array([ 7, 28])]
[array([ 4, 16])]
[array([ 8, 17])]
[array([1, 6])]
[array([ 6, 10])]
[array([6, 1])]
[array([ 5, 24])]
[array([ 3, 28])]
[array([ 2, 11])]
[array([ 3, 23])]
[array([ 6, 20])]
[array([ 1, 16])]
[array([4, 2])]
[array([ 6, 17])]
[array([ 5

[array([2, 9])]
[array([ 6, 28])]
[array([3, 7])]
[array([ 5, 26])]
[array([ 7, 12])]
[array([ 7, 27])]
[array([ 5, 15])]
[array([ 1, 15])]
[array([3, 4])]
[array([ 1, 15])]
[array([0, 8])]
[array([ 5, 24])]
[array([ 3, 21])]
[array([ 7, 13])]
[array([ 4, 15])]
[array([15,  6])]
[array([3, 9])]
[array([0, 8])]
[array([ 5, 20])]
[array([3, 4])]
[array([ 9, 12])]
[array([ 5, 26])]
[array([ 0, 19])]
[array([0, 5])]
[array([3, 0])]
[array([12, 19])]
[array([ 0, 14])]
[array([ 5, 12])]
[array([ 6, 16])]
[array([13, 25])]
[array([ 3, 13])]
[array([6, 3])]
[array([ 5, 20])]
[array([ 9, 15])]
[array([ 7, 16])]
[array([8, 1])]
[array([1, 1])]
[array([2, 2])]
[array([7, 7])]
[array([ 7, 21])]
[array([ 3, 20])]
[array([ 0, 19])]
[array([ 3, 20])]
[array([10, 20])]
[array([22,  8])]
[array([18, 21])]
[array([ 3, 24])]
[array([ 4, 26])]
[array([24,  8])]
[array([ 5, 21])]
[array([ 0, 23])]
[array([ 6, 16])]
[array([ 0, 29])]
[array([ 3, 24])]
[array([13, 10])]
[array([4, 2])]
[array([10,  5])]
[arr

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -343     |
| time/              |          |
|    fps             | 1123     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [22]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([2, 5]), None)

In [23]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_8
[array([12, 16])]
[array([ 6, 22])]
[array([ 5, 16])]
[array([3, 1])]
[array([ 3, 21])]
[array([ 5, 10])]
[array([ 3, 29])]
[array([ 0, 26])]
[array([ 2, 13])]
[array([ 0, 12])]
[array([ 0, 14])]
[array([ 3, 21])]
[array([0, 5])]
[array([ 4, 25])]
[array([ 7, 11])]
[array([1, 4])]
[array([ 1, 12])]
[array([ 1, 29])]
[array([ 0, 13])]
[array([4, 4])]
[array([ 6, 14])]
[array([4, 0])]
[array([1, 0])]
[array([24, 15])]
[array([ 1, 28])]
[array([ 5, 12])]
[array([ 6, 29])]
[array([ 1, 13])]
[array([ 0, 10])]
[array([ 0, 21])]
[array([ 5, 14])]
[array([3, 8])]
[array([ 1, 11])]
[array([ 5, 12])]
[array([0, 5])]
[array([ 2, 17])]
[array([ 0, 26])]
[array([0, 1])]
[array([ 0, 29])]
[array([27, 25])]
[array([ 5, 28])]
[array([ 5, 24])]
[array([11, 24])]
[array([ 7, 11])]
[array([ 2, 15])]
[array([ 2, 29])]
[array([ 1, 10])]
[array([ 0, 29])]
[array([ 0, 23])]
[array([25, 23])]
[array([26,  5])]
[array([6, 3])]
[array([ 1, 10])]
[array([4, 0])]
[array([ 3, 21])]
[ar

[array([ 5, 21])]
[array([5, 5])]
[array([2, 4])]
[array([2, 8])]
[array([11, 20])]
[array([ 4, 19])]
[array([ 7, 14])]
[array([2, 9])]
[array([ 3, 13])]
[array([ 2, 22])]
[array([ 5, 11])]
[array([2, 1])]
[array([ 0, 17])]
[array([5, 2])]
[array([9, 8])]
[array([ 5, 18])]
[array([ 1, 26])]
[array([1, 8])]
[array([ 0, 22])]
[array([ 3, 25])]
[array([ 5, 22])]
[array([ 4, 11])]
[array([7, 6])]
[array([2, 3])]
[array([ 1, 10])]
[array([ 3, 22])]
[array([ 4, 11])]
[array([5, 1])]
[array([2, 8])]
[array([ 1, 23])]
[array([1, 0])]
[array([ 6, 16])]
[array([ 7, 25])]
[array([14, 20])]
[array([ 4, 16])]
[array([5, 3])]
[array([ 3, 13])]
[array([1, 2])]
[array([ 2, 19])]
[array([5, 6])]
[array([1, 6])]
[array([ 2, 25])]
[array([ 4, 17])]
[array([11, 14])]
[array([ 2, 28])]
[array([ 5, 18])]
[array([1, 2])]
[array([ 8, 22])]
[array([5, 9])]
[array([ 2, 15])]
[array([ 6, 27])]
[array([ 5, 20])]
[array([ 6, 22])]
[array([ 1, 17])]
[array([ 1, 10])]
[array([1, 9])]
[array([ 7, 22])]
[array([ 0, 14

[array([ 1, 11])]
[array([ 2, 13])]
[array([ 2, 13])]
[array([ 2, 19])]
[array([ 7, 20])]
[array([ 2, 15])]
[array([ 7, 17])]
[array([1, 3])]
[array([7, 8])]
[array([9, 4])]
[array([ 5, 20])]
[array([ 0, 11])]
[array([ 4, 29])]
[array([ 6, 21])]
[array([ 4, 20])]
[array([5, 1])]
[array([8, 5])]
[array([14,  6])]
[array([ 4, 28])]
[array([ 3, 18])]
[array([ 1, 25])]
[array([5, 5])]
[array([ 6, 27])]
[array([ 1, 21])]
[array([ 3, 13])]
[array([ 0, 26])]
[array([ 5, 11])]
[array([ 5, 19])]
[array([5, 1])]
[array([ 3, 29])]
[array([ 6, 17])]
[array([ 2, 29])]
[array([ 6, 12])]
[array([ 4, 14])]
[array([ 5, 10])]
[array([ 7, 17])]
[array([ 3, 17])]
[array([ 3, 13])]
[array([6, 3])]
[array([3, 5])]
[array([ 1, 24])]
[array([19,  4])]
[array([1, 2])]
[array([ 3, 29])]
[array([0, 3])]
[array([ 3, 13])]
[array([ 9, 13])]
[array([3, 3])]
[array([2, 0])]
[array([ 2, 27])]
[array([5, 2])]
[array([ 5, 26])]
[array([ 4, 26])]
[array([10, 29])]
[array([ 6, 11])]
[array([ 1, 26])]
[array([ 0, 12])]
[a

In [24]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([ 2, 10]), None)

In [25]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_9
[array([ 5, 11])]
[array([3, 1])]
[array([0, 1])]
[array([ 4, 19])]
[array([ 3, 14])]
[array([ 2, 16])]
[array([6, 3])]
[array([14, 13])]
[array([24, 15])]
[array([5, 4])]
[array([0, 8])]
[array([18, 10])]
[array([7, 1])]
[array([ 0, 18])]
[array([ 1, 10])]
[array([5, 5])]
[array([6, 0])]
[array([4, 3])]
[array([ 9, 18])]
[array([ 2, 23])]
[array([ 1, 15])]
[array([ 3, 20])]
[array([ 5, 25])]
[array([ 6, 16])]
[array([19, 24])]
[array([ 4, 10])]
[array([ 0, 27])]
[array([ 2, 23])]
[array([1, 7])]
[array([ 1, 23])]
[array([ 1, 19])]
[array([ 0, 14])]
[array([2, 2])]
[array([3, 5])]
[array([ 2, 10])]
[array([ 0, 24])]
[array([ 2, 12])]
[array([6, 8])]
[array([ 4, 13])]
[array([ 2, 12])]
[array([5, 3])]
[array([ 4, 10])]
[array([4, 2])]
[array([ 2, 26])]
[array([ 2, 26])]
[array([ 4, 20])]
[array([4, 6])]
[array([ 6, 23])]
[array([0, 7])]
[array([ 1, 18])]
[array([0, 1])]
[array([ 3, 21])]
[array([ 0, 14])]
[array([ 3, 20])]
[array([ 0, 22])]
[array([1, 3])]
[

[array([ 8, 26])]
[array([20,  3])]
[array([14, 24])]
[array([3, 3])]
[array([ 8, 13])]
[array([ 4, 22])]
[array([10,  8])]
[array([ 1, 21])]
[array([ 7, 17])]
[array([ 1, 24])]
[array([ 3, 13])]
[array([6, 8])]
[array([ 0, 22])]
[array([5, 1])]
[array([ 5, 15])]
[array([ 1, 28])]
[array([3, 9])]
[array([0, 4])]
[array([ 4, 28])]
[array([ 0, 21])]
[array([15,  8])]
[array([ 2, 10])]
[array([ 7, 12])]
[array([ 3, 23])]
[array([ 4, 18])]
[array([ 3, 27])]
[array([ 3, 10])]
[array([6, 4])]
[array([ 0, 11])]
[array([ 3, 26])]
[array([ 0, 19])]
[array([1, 6])]
[array([ 3, 21])]
[array([5, 6])]
[array([ 2, 16])]
[array([ 8, 28])]
[array([ 3, 11])]
[array([ 1, 18])]
[array([3, 5])]
[array([ 2, 12])]
[array([ 0, 16])]
[array([ 3, 25])]
[array([3, 8])]
[array([ 4, 16])]
[array([ 0, 10])]
[array([ 7, 17])]
[array([ 0, 22])]
[array([3, 7])]
[array([ 3, 17])]
[array([ 2, 13])]
[array([2, 9])]
[array([3, 1])]
[array([11,  8])]
[array([ 4, 21])]
[array([2, 2])]
[array([ 0, 19])]
[array([ 0, 23])]
[a

[array([ 1, 20])]
[array([4, 5])]
[array([ 0, 12])]
[array([ 3, 18])]
[array([ 1, 25])]
[array([14, 16])]
[array([ 3, 23])]
[array([ 0, 15])]
[array([16, 19])]
[array([3, 9])]
[array([ 1, 17])]
[array([ 3, 22])]
[array([0, 6])]
[array([ 4, 18])]
[array([ 8, 19])]
[array([ 1, 16])]
[array([ 2, 11])]
[array([4, 6])]
[array([ 1, 13])]
[array([17, 10])]
[array([0, 3])]
[array([0, 6])]
[array([ 5, 18])]
[array([ 3, 23])]
[array([1, 7])]
[array([ 1, 29])]
[array([ 1, 14])]
[array([3, 0])]
[array([2, 6])]
[array([ 3, 26])]
[array([2, 2])]
[array([ 2, 14])]
[array([4, 2])]
[array([12, 24])]
[array([ 3, 18])]
[array([ 6, 12])]
[array([ 7, 29])]
[array([ 2, 10])]
[array([1, 3])]
[array([ 3, 27])]
[array([3, 6])]
[array([ 6, 27])]
[array([ 3, 20])]
[array([5, 0])]
[array([ 2, 25])]
[array([1, 9])]
[array([1, 6])]
[array([2, 8])]
[array([4, 7])]
[array([ 0, 20])]
[array([ 4, 28])]
[array([ 7, 25])]
[array([ 1, 24])]
[array([ 2, 13])]
[array([11, 15])]
[array([ 3, 29])]
[array([ 4, 26])]
[array([ 2

In [26]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([ 6, 24]), None)

In [27]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_10
[array([0, 3])]
[array([1, 8])]
[array([ 3, 21])]
[array([ 5, 26])]
[array([4, 9])]
[array([ 2, 23])]
[array([ 4, 15])]
[array([0, 6])]
[array([3, 1])]
[array([ 0, 13])]
[array([ 0, 24])]
[array([1, 9])]
[array([ 9, 21])]
[array([ 1, 16])]
[array([ 2, 11])]
[array([ 0, 10])]
[array([0, 5])]
[array([ 1, 15])]
[array([ 1, 29])]
[array([ 1, 13])]
[array([ 3, 21])]
[array([ 2, 10])]
[array([ 2, 12])]
[array([ 0, 23])]
[array([0, 2])]
[array([ 3, 20])]
[array([1, 1])]
[array([3, 1])]
[array([ 0, 20])]
[array([13, 20])]
[array([ 1, 20])]
[array([ 3, 17])]
[array([ 3, 17])]
[array([12,  8])]
[array([ 0, 17])]
[array([ 4, 13])]
[array([0, 3])]
[array([4, 3])]
[array([ 2, 23])]
[array([5, 3])]
[array([ 1, 17])]
[array([ 3, 18])]
[array([0, 0])]
[array([ 2, 28])]
[array([ 1, 18])]
[array([ 2, 19])]
[array([8, 7])]
[array([ 3, 11])]
[array([ 3, 14])]
[array([ 2, 15])]
[array([17,  4])]
[array([2, 4])]
[array([ 3, 21])]
[array([ 1, 17])]
[array([ 4, 26])]
[array([ 1, 

[array([13,  5])]
[array([2, 5])]
[array([ 2, 25])]
[array([ 1, 21])]
[array([ 4, 15])]
[array([1, 7])]
[array([ 1, 19])]
[array([3, 3])]
[array([3, 2])]
[array([3, 0])]
[array([ 2, 22])]
[array([ 0, 10])]
[array([ 1, 27])]
[array([ 0, 21])]
[array([1, 0])]
[array([ 3, 26])]
[array([ 0, 14])]
[array([4, 0])]
[array([6, 5])]
[array([4, 2])]
[array([ 2, 28])]
[array([5, 6])]
[array([ 0, 14])]
[array([1, 9])]
[array([3, 7])]
[array([2, 2])]
[array([ 0, 18])]
[array([ 3, 22])]
[array([ 0, 12])]
[array([4, 0])]
[array([ 1, 27])]
[array([0, 7])]
[array([ 4, 24])]
[array([ 1, 23])]
[array([ 0, 18])]
[array([0, 2])]
[array([ 0, 17])]
[array([1, 0])]
[array([0, 7])]
[array([ 8, 13])]
[array([9, 0])]
[array([ 0, 12])]
[array([1, 7])]
[array([12, 19])]
[array([2, 3])]
[array([2, 4])]
[array([2, 8])]
[array([ 1, 27])]
[array([ 1, 11])]
[array([ 2, 11])]
[array([ 3, 24])]
[array([ 3, 25])]
[array([ 3, 12])]
[array([ 5, 10])]
[array([ 0, 18])]
[array([2, 4])]
[array([15, 24])]
[array([1, 0])]
[array

[array([ 4, 14])]
[array([ 1, 19])]
[array([3, 6])]
[array([ 2, 18])]
[array([ 5, 16])]
[array([2, 2])]
[array([0, 8])]
[array([ 3, 16])]
[array([ 0, 15])]
[array([2, 7])]
[array([ 2, 11])]
[array([0, 1])]
[array([ 2, 17])]
[array([4, 0])]
[array([ 6, 22])]
[array([2, 1])]
[array([0, 9])]
[array([0, 3])]
[array([ 4, 13])]
[array([ 5, 24])]
[array([ 3, 13])]
[array([ 3, 16])]
[array([0, 2])]
[array([0, 5])]
[array([5, 1])]
[array([ 1, 11])]
[array([ 1, 22])]
[array([5, 1])]
[array([ 3, 27])]
[array([ 1, 27])]
[array([ 0, 10])]
[array([ 2, 29])]
[array([3, 9])]
[array([ 4, 10])]
[array([3, 8])]
[array([ 8, 20])]
[array([ 1, 23])]
[array([ 2, 19])]
[array([ 1, 28])]
[array([3, 0])]
[array([0, 4])]
[array([2, 7])]
[array([ 2, 28])]
[array([ 1, 14])]
[array([2, 8])]
[array([0, 2])]
[array([3, 4])]
[array([ 0, 11])]
[array([0, 8])]
[array([ 4, 21])]
[array([ 1, 17])]
[array([ 1, 11])]
[array([ 0, 10])]
[array([2, 7])]
[array([ 3, 16])]
[array([ 5, 26])]
[array([1, 8])]
[array([3, 7])]
[array

In [28]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([3, 6]), None)

In [29]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_11
[array([1, 4])]
[array([ 1, 18])]
[array([ 0, 11])]
[array([ 2, 17])]
[array([ 3, 15])]
[array([1, 8])]
[array([ 3, 18])]
[array([0, 2])]
[array([ 3, 18])]
[array([3, 8])]
[array([ 3, 24])]
[array([1, 2])]
[array([ 3, 11])]
[array([ 1, 28])]
[array([15,  6])]
[array([0, 6])]
[array([ 1, 12])]
[array([ 1, 11])]
[array([1, 4])]
[array([0, 0])]
[array([3, 0])]
[array([ 4, 20])]
[array([0, 2])]
[array([1, 1])]
[array([11, 17])]
[array([ 4, 23])]
[array([ 0, 27])]
[array([2, 2])]
[array([ 0, 23])]
[array([ 1, 18])]
[array([ 2, 17])]
[array([ 0, 12])]
[array([ 3, 11])]
[array([ 2, 13])]
[array([2, 5])]
[array([ 2, 22])]
[array([ 1, 15])]
[array([ 4, 20])]
[array([4, 3])]
[array([ 1, 13])]
[array([15,  3])]
[array([1, 6])]
[array([1, 2])]
[array([2, 6])]
[array([ 1, 28])]
[array([ 9, 24])]
[array([3, 0])]
[array([0, 6])]
[array([3, 3])]
[array([ 2, 23])]
[array([0, 0])]
[array([ 3, 11])]
[array([1, 3])]
[array([4, 7])]
[array([ 3, 29])]
[array([ 0, 22])]
[array([

[array([ 2, 28])]
[array([ 1, 28])]
[array([ 0, 24])]
[array([1, 7])]
[array([0, 6])]
[array([ 1, 18])]
[array([ 8, 25])]
[array([ 5, 23])]
[array([2, 7])]
[array([ 1, 21])]
[array([ 1, 13])]
[array([ 0, 11])]
[array([ 0, 14])]
[array([1, 0])]
[array([ 0, 16])]
[array([7, 0])]
[array([7, 0])]
[array([3, 8])]
[array([ 0, 26])]
[array([ 2, 17])]
[array([ 4, 18])]
[array([10, 21])]
[array([ 1, 11])]
[array([ 3, 28])]
[array([ 2, 18])]
[array([3, 1])]
[array([ 0, 12])]
[array([ 1, 10])]
[array([2, 4])]
[array([ 0, 15])]
[array([ 0, 20])]
[array([3, 1])]
[array([ 1, 24])]
[array([ 3, 21])]
[array([ 1, 28])]
[array([3, 4])]
[array([ 0, 12])]
[array([ 2, 17])]
[array([2, 7])]
[array([1, 1])]
[array([ 2, 29])]
[array([ 0, 18])]
[array([1, 4])]
[array([ 3, 16])]
[array([ 0, 25])]
[array([ 0, 26])]
[array([1, 2])]
[array([1, 1])]
[array([0, 2])]
[array([ 2, 25])]
[array([3, 5])]
[array([ 3, 22])]
[array([ 5, 19])]
[array([ 1, 19])]
[array([ 1, 20])]
[array([ 4, 21])]
[array([ 0, 18])]
[array([6,

[array([ 0, 16])]
[array([1, 2])]
[array([ 0, 11])]
[array([2, 1])]
[array([ 1, 17])]
[array([1, 7])]
[array([ 2, 28])]
[array([3, 3])]
[array([2, 9])]
[array([ 7, 14])]
[array([ 2, 24])]
[array([ 1, 22])]
[array([ 0, 11])]
[array([1, 3])]
[array([0, 7])]
[array([ 3, 13])]
[array([ 3, 15])]
[array([ 2, 16])]
[array([1, 2])]
[array([ 0, 12])]
[array([0, 1])]
[array([0, 3])]
[array([ 5, 18])]
[array([ 3, 26])]
[array([ 4, 28])]
[array([2, 4])]
[array([0, 0])]
[array([2, 0])]
[array([4, 5])]
[array([ 4, 28])]
[array([ 0, 14])]
[array([ 4, 25])]
[array([0, 2])]
[array([0, 5])]
[array([0, 5])]
[array([ 0, 20])]
[array([ 0, 25])]
[array([ 2, 26])]
[array([0, 8])]
[array([ 2, 15])]
[array([2, 2])]
[array([ 1, 20])]
[array([ 1, 22])]
[array([ 3, 26])]
[array([ 2, 14])]
[array([ 3, 28])]
[array([ 1, 17])]
[array([ 2, 10])]
[array([ 2, 24])]
[array([ 1, 27])]
[array([ 3, 25])]
[array([1, 8])]
[array([28,  4])]
[array([1, 8])]
[array([1, 2])]
[array([1, 6])]
[array([2, 0])]
[array([2, 8])]
[array

[array([ 1, 27])]
[array([ 2, 12])]
[array([ 1, 12])]
[array([ 4, 11])]
[array([ 3, 13])]
[array([2, 3])]
[array([3, 2])]
[array([ 1, 25])]
[array([ 1, 28])]
[array([ 2, 11])]
[array([ 1, 19])]
[array([1, 0])]
[array([1, 5])]
[array([ 1, 10])]
[array([ 2, 17])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -166     |
| time/              |          |
|    fps             | 1110     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [30]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([2, 0]), None)

In [31]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_12
[array([2, 1])]
[array([ 0, 14])]
[array([ 2, 14])]
[array([19,  1])]
[array([0, 2])]
[array([0, 8])]
[array([ 2, 17])]
[array([1, 7])]
[array([ 2, 28])]
[array([2, 0])]
[array([ 0, 12])]
[array([ 0, 27])]
[array([1, 9])]
[array([ 2, 19])]
[array([ 2, 25])]
[array([3, 8])]
[array([ 0, 13])]
[array([ 1, 20])]
[array([2, 7])]
[array([ 1, 13])]
[array([1, 3])]
[array([1, 6])]
[array([ 0, 23])]
[array([0, 5])]
[array([0, 3])]
[array([0, 2])]
[array([1, 1])]
[array([0, 9])]
[array([0, 8])]
[array([ 2, 15])]
[array([2, 7])]
[array([1, 8])]
[array([0, 2])]
[array([ 0, 29])]
[array([2, 2])]
[array([1, 0])]
[array([2, 3])]
[array([0, 4])]
[array([0, 2])]
[array([0, 2])]
[array([ 7, 23])]
[array([3, 2])]
[array([0, 6])]
[array([2, 8])]
[array([ 0, 20])]
[array([2, 1])]
[array([0, 2])]
[array([10,  3])]
[array([1, 0])]
[array([ 7, 13])]
[array([2, 3])]
[array([ 2, 14])]
[array([2, 3])]
[array([1, 1])]
[array([0, 6])]
[array([2, 0])]
[array([ 0, 24])]
[array([3, 3])]


[array([ 0, 28])]
[array([1, 0])]
[array([1, 4])]
[array([ 2, 22])]
[array([ 3, 17])]
[array([1, 9])]
[array([2, 7])]
[array([ 1, 22])]
[array([0, 6])]
[array([ 0, 10])]
[array([0, 0])]
[array([ 0, 10])]
[array([ 2, 11])]
[array([1, 2])]
[array([1, 2])]
[array([ 1, 13])]
[array([ 0, 11])]
[array([0, 0])]
[array([ 0, 24])]
[array([0, 4])]
[array([1, 5])]
[array([ 0, 22])]
[array([0, 3])]
[array([1, 8])]
[array([1, 4])]
[array([3, 7])]
[array([ 4, 16])]
[array([3, 0])]
[array([ 0, 15])]
[array([0, 3])]
[array([ 1, 22])]
[array([ 2, 11])]
[array([2, 3])]
[array([0, 0])]
[array([ 2, 16])]
[array([ 1, 21])]
[array([ 0, 27])]
[array([ 2, 28])]
[array([1, 3])]
[array([3, 9])]
[array([1, 2])]
[array([2, 0])]
[array([0, 1])]
[array([ 1, 24])]
[array([ 7, 24])]
[array([ 1, 12])]
[array([2, 3])]
[array([ 0, 17])]
[array([ 0, 10])]
[array([ 0, 25])]
[array([ 5, 11])]
[array([ 0, 27])]
[array([1, 8])]
[array([ 0, 17])]
[array([ 2, 11])]
[array([ 3, 10])]
[array([ 2, 24])]
[array([1, 1])]
[array([ 0

[array([2, 4])]
[array([ 2, 24])]
[array([1, 5])]
[array([1, 5])]
[array([ 0, 28])]
[array([1, 7])]
[array([ 0, 18])]
[array([1, 4])]
[array([2, 9])]
[array([0, 1])]
[array([ 0, 22])]
[array([ 2, 16])]
[array([5, 4])]
[array([ 0, 11])]
[array([2, 3])]
[array([ 0, 10])]
[array([ 2, 10])]
[array([ 2, 12])]
[array([ 1, 14])]
[array([2, 5])]
[array([ 0, 12])]
[array([1, 0])]
[array([1, 8])]
[array([ 2, 13])]
[array([1, 9])]
[array([0, 1])]
[array([ 0, 23])]
[array([ 0, 23])]
[array([4, 1])]
[array([1, 5])]
[array([21,  3])]
[array([ 1, 28])]
[array([0, 3])]
[array([ 2, 22])]
[array([ 0, 11])]
[array([ 7, 25])]
[array([0, 1])]
[array([ 3, 12])]
[array([15,  6])]
[array([ 0, 28])]
[array([ 2, 28])]
[array([ 1, 13])]
[array([ 2, 24])]
[array([0, 2])]
[array([ 1, 26])]
[array([0, 4])]
[array([ 6, 19])]
[array([ 0, 21])]
[array([ 0, 10])]
[array([ 0, 17])]
[array([2, 8])]
[array([0, 9])]
[array([ 1, 29])]
[array([2, 4])]
[array([2, 1])]
[array([ 1, 24])]
[array([ 1, 22])]
[array([2, 0])]
[array

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -128     |
| time/              |          |
|    fps             | 1120     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [32]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([ 0, 15]), None)

In [33]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_13
[array([1, 0])]
[array([ 2, 12])]
[array([0, 0])]
[array([0, 9])]
[array([ 0, 18])]
[array([0, 8])]
[array([1, 4])]
[array([ 2, 10])]
[array([1, 6])]
[array([1, 5])]
[array([2, 0])]
[array([0, 8])]
[array([0, 3])]
[array([0, 9])]
[array([ 1, 11])]
[array([0, 0])]
[array([0, 3])]
[array([ 6, 17])]
[array([0, 4])]
[array([ 0, 19])]
[array([ 1, 29])]
[array([0, 2])]
[array([ 2, 19])]
[array([2, 0])]
[array([ 2, 12])]
[array([0, 3])]
[array([ 1, 23])]
[array([1, 1])]
[array([ 0, 11])]
[array([0, 3])]
[array([3, 0])]
[array([0, 4])]
[array([0, 1])]
[array([ 0, 11])]
[array([1, 0])]
[array([ 0, 24])]
[array([0, 4])]
[array([ 1, 13])]
[array([ 2, 13])]
[array([0, 5])]
[array([0, 0])]
[array([0, 9])]
[array([ 0, 22])]
[array([1, 1])]
[array([ 0, 26])]
[array([0, 0])]
[array([ 0, 11])]
[array([2, 2])]
[array([ 1, 16])]
[array([ 1, 18])]
[array([ 0, 12])]
[array([1, 0])]
[array([1, 4])]
[array([ 1, 13])]
[array([1, 1])]
[array([0, 5])]
[array([1, 2])]
[array([1, 1])

[array([1, 9])]
[array([0, 3])]
[array([1, 6])]
[array([0, 6])]
[array([0, 4])]
[array([0, 4])]
[array([4, 9])]
[array([0, 7])]
[array([1, 8])]
[array([1, 7])]
[array([0, 0])]
[array([2, 1])]
[array([1, 1])]
[array([0, 9])]
[array([ 2, 11])]
[array([1, 2])]
[array([ 1, 11])]
[array([ 0, 13])]
[array([ 0, 16])]
[array([ 0, 14])]
[array([1, 3])]
[array([ 6, 11])]
[array([1, 8])]
[array([2, 6])]
[array([6, 4])]
[array([ 2, 25])]
[array([0, 0])]
[array([ 0, 11])]
[array([0, 0])]
[array([0, 2])]
[array([ 2, 10])]
[array([0, 2])]
[array([1, 7])]
[array([ 2, 16])]
[array([1, 9])]
[array([0, 4])]
[array([ 2, 23])]
[array([0, 1])]
[array([2, 2])]
[array([ 5, 27])]
[array([ 0, 17])]
[array([ 0, 13])]
[array([2, 1])]
[array([2, 8])]
[array([ 1, 20])]
[array([2, 0])]
[array([2, 7])]
[array([ 0, 18])]
[array([0, 4])]
[array([ 1, 12])]
[array([1, 1])]
[array([0, 7])]
[array([ 1, 29])]
[array([ 2, 26])]
[array([0, 3])]
[array([0, 5])]
[array([2, 0])]
[array([3, 8])]
[array([1, 4])]
[array([1, 0])]
[a

[array([0, 3])]
[array([ 0, 25])]
[array([ 0, 23])]
[array([0, 6])]
[array([ 0, 11])]
[array([ 0, 17])]
[array([0, 0])]
[array([0, 3])]
[array([3, 6])]
[array([ 0, 17])]
[array([ 1, 12])]
[array([0, 4])]
[array([2, 7])]
[array([0, 4])]
[array([2, 0])]
[array([0, 6])]
[array([0, 1])]
[array([ 1, 24])]
[array([0, 5])]
[array([ 0, 19])]
[array([1, 2])]
[array([0, 7])]
[array([ 2, 10])]
[array([1, 0])]
[array([ 0, 23])]
[array([ 1, 13])]
[array([ 1, 23])]
[array([1, 2])]
[array([2, 0])]
[array([0, 3])]
[array([ 2, 10])]
[array([0, 5])]
[array([2, 9])]
[array([ 2, 15])]
[array([0, 2])]
[array([ 1, 23])]
[array([ 1, 27])]
[array([ 1, 13])]
[array([ 1, 13])]
[array([ 0, 24])]
[array([0, 7])]
[array([0, 0])]
[array([0, 7])]
[array([0, 7])]
[array([1, 4])]
[array([1, 4])]
[array([ 2, 14])]
[array([ 0, 13])]
[array([ 1, 11])]
[array([0, 0])]
[array([ 0, 19])]
[array([ 1, 10])]
[array([ 0, 13])]
[array([ 0, 14])]
[array([1, 2])]
[array([ 0, 11])]
[array([0, 8])]
[array([1, 4])]
[array([0, 6])]
[a

[array([0, 8])]
[array([ 1, 10])]
[array([2, 0])]
[array([0, 5])]
[array([ 1, 11])]
[array([1, 4])]
[array([0, 3])]
[array([0, 2])]
[array([0, 8])]
[array([0, 1])]
[array([0, 7])]
[array([1, 1])]
[array([ 1, 12])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -78.7    |
| time/              |          |
|    fps             | 1112     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [34]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 2]), None)

In [35]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_14
[array([0, 0])]
[array([1, 1])]
[array([0, 3])]
[array([1, 2])]
[array([0, 3])]
[array([0, 8])]
[array([ 1, 17])]
[array([1, 4])]
[array([ 0, 11])]
[array([ 0, 11])]
[array([1, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 7])]
[array([0, 3])]
[array([1, 9])]
[array([1, 7])]
[array([ 0, 22])]
[array([ 0, 27])]
[array([0, 7])]
[array([0, 3])]
[array([0, 3])]
[array([0, 3])]
[array([0, 2])]
[array([0, 8])]
[array([1, 0])]
[array([0, 7])]
[array([0, 3])]
[array([0, 8])]
[array([ 1, 10])]
[array([2, 0])]
[array([0, 4])]
[array([1, 8])]
[array([1, 7])]
[array([0, 8])]
[array([0, 7])]
[array([0, 0])]
[array([ 1, 16])]
[array([0, 5])]
[array([1, 4])]
[array([0, 1])]
[array([0, 3])]
[array([0, 5])]
[array([0, 8])]
[array([0, 3])]
[array([0, 3])]
[array([0, 2])]
[array([0, 3])]
[array([0, 3])]
[array([0, 1])]
[array([0, 5])]
[array([0, 3])]
[array([0, 0])]
[array([0, 5])]
[array([ 0, 12])]
[array([1, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 6])]
[array([0,

[array([1, 7])]
[array([1, 0])]
[array([ 0, 21])]
[array([0, 4])]
[array([0, 5])]
[array([0, 1])]
[array([0, 0])]
[array([1, 5])]
[array([0, 7])]
[array([0, 1])]
[array([1, 4])]
[array([ 1, 26])]
[array([0, 5])]
[array([ 0, 14])]
[array([0, 9])]
[array([1, 9])]
[array([0, 4])]
[array([ 1, 13])]
[array([ 0, 13])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([ 0, 16])]
[array([1, 2])]
[array([0, 1])]
[array([0, 0])]
[array([1, 9])]
[array([1, 0])]
[array([0, 3])]
[array([0, 3])]
[array([0, 1])]
[array([ 0, 15])]
[array([0, 2])]
[array([1, 3])]
[array([0, 3])]
[array([0, 2])]
[array([ 1, 16])]
[array([0, 0])]
[array([1, 0])]
[array([ 1, 10])]
[array([0, 0])]
[array([1, 9])]
[array([1, 2])]
[array([0, 1])]
[array([ 1, 25])]
[array([0, 9])]
[array([0, 0])]
[array([ 0, 14])]
[array([0, 2])]
[array([0, 0])]
[array([0, 7])]
[array([ 0, 11])]
[array([1, 4])]
[array([1, 2])]
[array([0, 2])]
[array([0, 0])]
[array([0, 6])]
[array([1, 2])]
[array([1, 4])]
[array([0, 8])]
[array([ 0, 10])

[array([ 0, 23])]
[array([1, 6])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 3])]
[array([1, 0])]
[array([0, 2])]
[array([0, 3])]
[array([0, 4])]
[array([0, 3])]
[array([0, 0])]
[array([ 0, 12])]
[array([0, 1])]
[array([1, 5])]
[array([ 0, 14])]
[array([0, 9])]
[array([1, 2])]
[array([1, 6])]
[array([0, 3])]
[array([0, 0])]
[array([ 1, 28])]
[array([0, 2])]
[array([1, 9])]
[array([0, 9])]
[array([0, 5])]
[array([ 1, 27])]
[array([0, 3])]
[array([1, 6])]
[array([ 1, 14])]
[array([0, 5])]
[array([ 1, 18])]
[array([0, 2])]
[array([ 0, 11])]
[array([0, 3])]
[array([0, 4])]
[array([1, 3])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([ 0, 14])]
[array([0, 3])]
[array([0, 6])]
[array([0, 5])]
[array([0, 5])]
[array([0, 0])]
[array([0, 3])]
[array([0, 6])]
[array([0, 1])]
[array([ 1, 11])]
[array([ 2, 15])]
[array([ 0, 11])]
[array([0, 3])]
[array([1, 0])]
[array([0, 5])]
[array([ 1, 11])]
[array([1, 3])]
[array([0, 4])]
[array([1, 1])]
[array([ 0, 13])]
[array([ 1, 

In [36]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([ 0, 12]), None)

In [37]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_15
[array([1, 0])]
[array([1, 5])]
[array([0, 3])]
[array([0, 0])]
[array([1, 4])]
[array([0, 3])]
[array([1, 0])]
[array([1, 1])]
[array([ 0, 10])]
[array([ 0, 18])]
[array([0, 0])]
[array([ 0, 17])]
[array([0, 1])]
[array([0, 9])]
[array([0, 0])]
[array([0, 4])]
[array([0, 9])]
[array([0, 6])]
[array([0, 3])]
[array([ 0, 10])]
[array([0, 9])]
[array([ 0, 10])]
[array([0, 4])]
[array([0, 3])]
[array([0, 3])]
[array([0, 2])]
[array([0, 2])]
[array([0, 3])]
[array([1, 8])]
[array([1, 0])]
[array([ 0, 12])]
[array([ 0, 14])]
[array([ 0, 11])]
[array([0, 8])]
[array([0, 7])]
[array([0, 0])]
[array([0, 3])]
[array([3, 5])]
[array([0, 5])]
[array([1, 9])]
[array([0, 6])]
[array([0, 3])]
[array([ 0, 25])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 5])]
[array([0, 5])]
[array([0, 0])]
[array([0, 8])]
[array([0, 6])]
[array([ 0, 11])]
[array([0, 9])]
[array([0, 2])]
[array([0, 0])]
[array([ 0, 14])]
[array([0, 9])]
[array([0, 2])]
[array([ 1, 11])]
[a

[array([0, 1])]
[array([0, 4])]
[array([ 0, 11])]
[array([ 0, 23])]
[array([ 2, 15])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([1, 9])]
[array([0, 2])]
[array([0, 0])]
[array([1, 9])]
[array([ 0, 15])]
[array([ 1, 12])]
[array([0, 1])]
[array([ 0, 16])]
[array([ 0, 10])]
[array([0, 4])]
[array([0, 5])]
[array([0, 1])]
[array([0, 9])]
[array([0, 9])]
[array([0, 4])]
[array([0, 5])]
[array([1, 4])]
[array([1, 0])]
[array([0, 8])]
[array([0, 2])]
[array([1, 3])]
[array([ 0, 13])]
[array([ 0, 15])]
[array([1, 6])]
[array([0, 5])]
[array([0, 9])]
[array([1, 3])]
[array([0, 7])]
[array([0, 2])]
[array([1, 7])]
[array([ 0, 10])]
[array([ 0, 10])]
[array([0, 1])]
[array([ 0, 11])]
[array([0, 6])]
[array([ 0, 11])]
[array([0, 6])]
[array([0, 0])]
[array([1, 1])]
[array([ 0, 11])]
[array([0, 3])]
[array([1, 5])]
[array([0, 1])]
[array([0, 2])]
[array([1, 2])]
[array([0, 4])]
[array([0, 2])]
[array([1, 3])]
[array([0, 5])]
[array([0, 0])]
[array([0, 7])]
[array([ 0, 13])]
[array([1,

[array([1, 8])]
[array([0, 0])]
[array([ 0, 10])]
[array([0, 5])]
[array([0, 9])]
[array([1, 0])]
[array([1, 7])]
[array([0, 1])]
[array([1, 7])]
[array([0, 1])]
[array([1, 3])]
[array([0, 6])]
[array([0, 5])]
[array([0, 6])]
[array([1, 6])]
[array([1, 2])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([1, 4])]
[array([1, 1])]
[array([1, 7])]
[array([0, 2])]
[array([0, 3])]
[array([1, 6])]
[array([0, 0])]
[array([0, 6])]
[array([1, 4])]
[array([0, 1])]
[array([ 1, 10])]
[array([0, 0])]
[array([0, 3])]
[array([0, 1])]
[array([1, 2])]
[array([1, 1])]
[array([0, 1])]
[array([1, 0])]
[array([0, 3])]
[array([ 0, 11])]
[array([0, 8])]
[array([0, 5])]
[array([0, 4])]
[array([0, 2])]
[array([ 0, 10])]
[array([ 0, 14])]
[array([0, 5])]
[array([0, 6])]
[array([ 0, 13])]
[array([1, 9])]
[array([1, 3])]
[array([0, 0])]
[array([ 0, 15])]
[array([0, 9])]
[array([0, 2])]
[array([0, 1])]
[array([0, 6])]
[array([1, 6])]
[array([ 0, 16])]
[array([0, 7])]
[array([ 0, 14])]
[array([1, 6])]
[array

In [38]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([ 0, 19]), None)

In [39]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_16
[array([0, 1])]
[array([0, 1])]
[array([0, 3])]
[array([0, 5])]
[array([0, 4])]
[array([1, 4])]
[array([0, 1])]
[array([0, 3])]
[array([0, 7])]
[array([0, 9])]
[array([0, 0])]
[array([0, 4])]
[array([0, 0])]
[array([0, 2])]
[array([0, 1])]
[array([0, 3])]
[array([0, 5])]
[array([0, 3])]
[array([0, 2])]
[array([0, 4])]
[array([0, 4])]
[array([0, 3])]
[array([0, 2])]
[array([0, 0])]
[array([0, 3])]
[array([0, 5])]
[array([1, 0])]
[array([0, 5])]
[array([0, 0])]
[array([0, 9])]
[array([0, 2])]
[array([0, 4])]
[array([0, 6])]
[array([0, 9])]
[array([1, 3])]
[array([0, 0])]
[array([0, 5])]
[array([0, 4])]
[array([0, 2])]
[array([1, 9])]
[array([0, 2])]
[array([0, 7])]
[array([0, 1])]
[array([ 0, 10])]
[array([0, 0])]
[array([0, 7])]
[array([0, 3])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 4])]
[array([ 1, 11])]
[array([0, 2])]
[array([0, 2])]
[array([0, 6])]
[array([0, 2])]
[array([0, 6])]
[array([0, 6])]
[array([ 0, 11])]
[array([1, 2])]
[arr

[array([0, 6])]
[array([0, 0])]
[array([0, 2])]
[array([1, 7])]
[array([0, 4])]
[array([0, 3])]
[array([0, 3])]
[array([0, 2])]
[array([0, 1])]
[array([1, 5])]
[array([ 0, 12])]
[array([2, 4])]
[array([1, 1])]
[array([0, 4])]
[array([ 0, 15])]
[array([ 0, 12])]
[array([0, 5])]
[array([0, 2])]
[array([0, 5])]
[array([0, 4])]
[array([ 0, 10])]
[array([0, 3])]
[array([0, 4])]
[array([0, 1])]
[array([0, 6])]
[array([0, 2])]
[array([0, 4])]
[array([0, 1])]
[array([1, 7])]
[array([0, 5])]
[array([0, 1])]
[array([0, 7])]
[array([1, 4])]
[array([0, 7])]
[array([0, 3])]
[array([0, 9])]
[array([0, 0])]
[array([0, 8])]
[array([0, 3])]
[array([0, 1])]
[array([0, 5])]
[array([0, 0])]
[array([0, 4])]
[array([0, 3])]
[array([0, 0])]
[array([0, 5])]
[array([0, 8])]
[array([0, 6])]
[array([0, 3])]
[array([0, 4])]
[array([ 0, 11])]
[array([0, 1])]
[array([ 0, 18])]
[array([0, 9])]
[array([0, 4])]
[array([0, 0])]
[array([0, 7])]
[array([0, 2])]
[array([0, 5])]
[array([0, 1])]
[array([0, 4])]
[array([0, 2

[array([0, 0])]
[array([ 0, 15])]
[array([0, 4])]
[array([0, 1])]
[array([0, 3])]
[array([1, 1])]
[array([1, 0])]
[array([0, 5])]
[array([0, 5])]
[array([0, 3])]
[array([0, 7])]
[array([0, 0])]
[array([0, 7])]
[array([0, 2])]
[array([0, 1])]
[array([1, 4])]
[array([1, 2])]
[array([0, 5])]
[array([0, 1])]
[array([0, 8])]
[array([ 0, 10])]
[array([0, 7])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 9])]
[array([0, 0])]
[array([2, 1])]
[array([0, 3])]
[array([0, 2])]
[array([0, 6])]
[array([0, 1])]
[array([0, 6])]
[array([0, 5])]
[array([0, 3])]
[array([ 1, 11])]
[array([1, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([18,  0])]
[array([0, 9])]
[array([1, 1])]
[array([0, 4])]
[array([0, 2])]
[array([0, 4])]
[array([0, 3])]
[array([0, 5])]
[array([0, 5])]
[array([0, 0])]
[array([0, 6])]
[array([0, 2])]
[array([0, 3])]
[array([0, 5])]
[array([0, 4])]
[array([0, 1])]
[array([0, 6])]
[array([0, 2])]
[array([0, 3])]


In [40]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 5]), None)

In [41]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_17
[array([0, 4])]
[array([0, 3])]
[array([0, 5])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([ 0, 10])]
[array([ 1, 10])]
[array([0, 0])]
[array([0, 4])]
[array([0, 0])]
[array([0, 0])]
[array([0, 3])]
[array([0, 4])]
[array([0, 4])]
[array([0, 3])]
[array([0, 1])]
[array([0, 2])]
[array([ 0, 11])]
[array([ 0, 26])]
[array([0, 3])]
[array([0, 1])]
[array([1, 4])]
[array([1, 5])]
[array([0, 2])]
[array([0, 1])]
[array([0, 2])]
[array([0, 3])]
[array([1, 4])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 3])]
[array([2, 0])]
[array([0, 4])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([ 0, 12])]
[array([0, 7])]
[array([0, 1])]
[array([0, 3])]
[array([0, 2])]
[array([0, 8])]
[array([0, 0])]
[array([0, 0])]
[array([0, 3])]
[array([0, 3])]
[array([0, 4])]
[array([0, 1])]
[array([0, 1])]
[array([0, 3])]
[array([0, 2])]
[array([0, 2])]
[array([ 0, 14])]
[array([0, 4])]
[array([0, 2])]
[array([0, 6])]
[array([0, 2])]
[array([0, 4])

[array([0, 1])]
[array([0, 0])]
[array([0, 2])]
[array([1, 2])]
[array([0, 0])]
[array([1, 3])]
[array([0, 3])]
[array([0, 4])]
[array([0, 1])]
[array([1, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 3])]
[array([0, 3])]
[array([0, 7])]
[array([0, 0])]
[array([0, 1])]
[array([0, 5])]
[array([1, 2])]
[array([0, 2])]
[array([0, 4])]
[array([0, 0])]
[array([ 0, 10])]
[array([1, 0])]
[array([0, 0])]
[array([27,  0])]
[array([0, 3])]
[array([0, 4])]
[array([0, 0])]
[array([0, 0])]
[array([0, 8])]
[array([0, 2])]
[array([0, 9])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 3])]
[array([2, 0])]
[array([0, 0])]
[array([0, 0])]
[array([ 0, 13])]
[array([ 0, 12])]
[array([0, 1])]
[array([0, 5])]
[array([0, 1])]
[array([0, 3])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([ 0, 13])]
[array([0, 2])]
[array([0, 2])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 1])]
[array([0, 4])]
[array([0, 3])

[array([0, 3])]
[array([0, 3])]
[array([ 0, 11])]
[array([0, 3])]
[array([0, 2])]
[array([0, 5])]
[array([0, 7])]
[array([0, 5])]
[array([0, 5])]
[array([0, 0])]
[array([0, 0])]
[array([0, 7])]
[array([0, 6])]
[array([0, 3])]
[array([0, 2])]
[array([1, 0])]
[array([0, 1])]
[array([0, 3])]
[array([0, 2])]
[array([0, 0])]
[array([0, 4])]
[array([2, 9])]
[array([ 0, 15])]
[array([0, 1])]
[array([0, 9])]
[array([0, 0])]
[array([0, 0])]
[array([ 0, 11])]
[array([0, 2])]
[array([0, 1])]
[array([0, 4])]
[array([0, 8])]
[array([0, 0])]
[array([0, 0])]
[array([1, 5])]
[array([1, 2])]
[array([0, 0])]
[array([1, 2])]
[array([0, 0])]
[array([0, 5])]
[array([0, 1])]
[array([0, 3])]
[array([0, 3])]
[array([0, 0])]
[array([0, 5])]
[array([0, 5])]
[array([0, 7])]
[array([0, 4])]
[array([ 0, 10])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 3])]
[array([0, 5])]
[array([0, 0])]
[array([0, 1])]
[array([ 0, 13])]
[array([0, 7])]
[array([0, 2])]
[array([0, 2])]
[array([0, 5])]
[array([0, 4])

[array([0, 3])]
[array([0, 3])]
[array([0, 5])]
[array([2, 4])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 3])]
[array([0, 0])]
[array([1, 1])]
[array([0, 3])]
[array([0, 3])]
[array([0, 6])]
[array([0, 2])]
[array([0, 2])]
[array([0, 4])]
[array([0, 0])]
[array([0, 5])]
[array([0, 0])]
[array([0, 2])]
[array([0, 4])]
[array([0, 7])]
[array([0, 7])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -24.4    |
| time/              |          |
|    fps             | 1106     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [42]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([ 0, 10]), None)

In [43]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_18
[array([0, 2])]
[array([0, 1])]
[array([0, 1])]
[array([0, 7])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 2])]
[array([0, 2])]
[array([0, 1])]
[array([0, 2])]
[array([0, 4])]
[array([0, 5])]
[array([0, 2])]
[array([0, 3])]
[array([0, 1])]
[array([0, 6])]
[array([0, 4])]
[array([0, 4])]
[array([ 0, 13])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 4])]
[array([0, 2])]
[array([0, 0])]
[array([0, 4])]
[array([0, 3])]
[array([0, 1])]
[array([0, 1])]
[array([0, 3])]
[array([0, 3])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 1])]
[array([0, 1])]
[array([1, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([

[array([0, 2])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 6])]
[array([0, 4])]
[array([0, 3])]
[array([0, 9])]
[array([0, 1])]
[array([0, 3])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 4])]
[array([0, 1])]
[array([0, 4])]
[array([0, 4])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 4])]
[array([0, 3])]
[array([0, 1])]
[array([0, 4])]
[array([0, 0])]
[array([0, 5])]
[array([0, 3])]
[array([0, 1])]
[array([0, 2])]
[array([0, 3])]
[array([0, 3])]
[array([0, 4])]
[array([0, 4])]
[array([0, 4])]
[array([0, 3])]
[array([0, 0])]
[array([0, 2])]
[array([0, 3])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([0, 3])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 2])]
[array([0, 1])]
[array([

[array([0, 3])]
[array([0, 3])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 3])]
[array([0, 8])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([ 0, 14])]
[array([0, 1])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 8])]
[array([1, 0])]
[array([0, 0])]
[array([0, 3])]
[array([0, 2])]
[array([0, 4])]
[array([0, 3])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 7])]
[array([0, 3])]
[array([0, 0])]
[array([0, 2])]
[array([ 0, 14])]
[array([0, 1])]
[array([0, 5])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([ 0, 13])]
[array([0, 4])]
[array([0, 3])]
[array([0, 6])]
[array([0, 3])]
[array([0, 1])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 4])]
[array([0, 0])]
[array([0, 9])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 4])]
[array([0, 1])]
[array([0, 3])]
[array([0, 4])]
[array([0, 2])]
[a

In [44]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 1]), None)

In [45]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_19
[array([0, 3])]
[array([0, 0])]
[array([0, 2])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([0, 3])]
[array([0, 1])]
[array([0, 0])]
[array([0, 3])]
[array([0, 5])]
[array([0, 0])]
[array([0, 3])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 3])]
[array([0, 1])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([ 0, 27])]
[array([0, 4])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 1])]
[array([0, 3])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 2])]
[array([ 0, 13])]
[array([0, 2])]
[array([0, 3])]
[array([0, 3])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 1])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 3])]
[array([0, 2])]
[array([0, 2])]
[array

[array([0, 1])]
[array([0, 2])]
[array([0, 1])]
[array([0, 3])]
[array([0, 0])]
[array([0, 1])]
[array([ 0, 11])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 2])]
[array([0, 2])]
[array([0, 0])]
[array([0, 3])]
[array([0, 4])]
[array([0, 1])]
[array([0, 4])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 3])]
[array([0, 2])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 2])]
[array([0, 2])]
[array([0, 0])]
[array([1, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 3])]
[array([0, 2])]
[array([0, 3])]
[array([0, 3])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 7])]
[array([0, 3])]
[array([0, 0])]
[array([ 0, 19])]
[array([0, 2])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[arr

[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([1, 2])]
[array([0, 0])]
[array([0, 2])]
[array([0, 3])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([0, 9])]
[array([0, 1])]
[array([0, 0])]
[array([0, 4])]
[array([0, 4])]
[array([0, 1])]
[array([0, 0])]
[array([0, 3])]
[array([0, 2])]
[array([1, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([0, 3])]
[array([0, 2])]
[array([0, 1])]
[array([0, 2])]
[array([0, 1])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([0, 4])]
[array([0, 2])]
[array([0, 0])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 4])]
[array([0, 1])]
[array([0, 3])]
[array([0, 2])]
[array([0, 0])]
[array([0, 4])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 7])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 3])]
[array([0, 3])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([0, 1])]
[array([

In [46]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [47]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_20
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 2])]
[array([0, 0])]
[array([0, 2])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([ 0, 15])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 9])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 3])]
[array([

[array([0, 0])]
[array([0, 1])]
[array([ 0, 22])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 2])]
[array([0, 3])]
[array([0, 4])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 4])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 2])]
[array([0, 0])]
[array([0, 4])]
[array([0, 0])]
[array

[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 7])]
[array([0, 1])]
[array([0, 3])]
[array([0, 1])]
[array([0, 1])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 6])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 1])]
[array([

In [48]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [49]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_21
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 1])]
[array([0, 1])]
[array([0, 1])]
[array([0, 1])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([0, 1])]
[array([

[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 2])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 3])]
[array([0, 1])]
[array([0, 1])]
[array([0, 2])]
[array([0, 5])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([ 0, 13])]
[array([0, 5])]
[array([0, 0])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 3])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array

In [50]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [51]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_22
[array([0, 0])]
[array([2, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 9])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 3])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 4])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -10.3    |
| time/              |          |
|    fps             | 1111     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [52]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [53]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_23
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([ 0, 21])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 9])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [54]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [55]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_24
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 2])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([ 0, 12])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array

[array([0, 1])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.6     |
| time/              |          |
|    fps             | 1119     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [56]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [57]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_25
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -9.05    |
| time/              |          |
|    fps             | 1122     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [58]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [59]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_26
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([ 0, 12])]
[array([0, 2])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [60]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [61]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_27
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 2])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.85    |
| time/              |          |
|    fps             | 1105     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [62]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [63]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_28
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.4     |
| time/              |          |
|    fps             | 1115     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [64]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [65]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_29
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.55    |
| time/              |          |
|    fps             | 1122     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [66]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [67]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_30
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.3     |
| time/              |          |
|    fps             | 1098     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [68]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [69]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_31
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.9     |
| time/              |          |
|    fps             | 1112     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [70]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [71]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_32
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.5     |
| time/              |          |
|    fps             | 1118     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [72]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [73]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_33
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.3     |
| time/              |          |
|    fps             | 1107     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [74]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [75]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_34
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [76]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [77]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_35
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [78]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [79]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_36
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -7.9     |
| time/              |          |
|    fps             | 1101     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [80]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [81]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_37
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 3])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.5     |
| time/              |          |
|    fps             | 1105     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [82]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [83]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_38
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.6     |
| time/              |          |
|    fps             | 1114     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [84]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [85]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_39
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.1     |
| time/              |          |
|    fps             | 1121     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [86]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [87]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_40
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [88]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [89]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_41
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.1     |
| time/              |          |
|    fps             | 1117     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [90]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [91]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_42
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([ 0, 11])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [92]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [93]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_43
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [94]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [95]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_44
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [96]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [97]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_45
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [98]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [99]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_46
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -7.9     |
| time/              |          |
|    fps             | 1119     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [100]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [101]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_47
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.2     |
| time/              |          |
|    fps             | 1120     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [102]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [103]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_48
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.85    |
| time/              |          |
|    fps             | 1119     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [104]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [105]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_49
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [106]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [107]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_50
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.4     |
| time/              |          |
|    fps             | 1119     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [108]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [109]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_51
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.2     |
| time/              |          |
|    fps             | 1117     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [110]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [111]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_52
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.4     |
| time/              |          |
|    fps             | 1111     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [112]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [113]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_53
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.4     |
| time/              |          |
|    fps             | 1118     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [114]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [115]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_54
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.2     |
| time/              |          |
|    fps             | 1117     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [116]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [117]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_55
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [118]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [119]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_56
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.9     |
| time/              |          |
|    fps             | 1097     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [120]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [121]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_57
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -7.6     |
| time/              |          |
|    fps             | 1119     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [122]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [123]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_58
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.3     |
| time/              |          |
|    fps             | 1092   

In [124]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [125]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_59
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.5     |
| time/              |          |
|    fps             | 1104     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [126]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [127]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_60
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.6     |
| time/              |          |
|    fps             | 1103     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [128]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [129]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_61
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.3     |
| time/              |          |
|    fps             | 1103     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [130]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [131]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_62
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.7     |
| time/              |          |
|    fps             | 1103     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [132]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [133]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_63
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [134]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [135]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_64
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.8     |
| time/              |          |
|    fps             | 1114     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [136]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [137]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_65
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.6     |
| time/              |          |
|    fps             | 1114     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [138]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [139]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_66
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 1])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8       |
| time/              |          |
|    fps             | 1115     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [140]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [141]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_67
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.6     |
| time/              |          |
|    fps             | 1107     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [142]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [143]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_68
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [144]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [145]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_69
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.2     |
| time/              |          |
|    fps             | 1110     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [146]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [147]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_70
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.1     |
| time/              |          |
|    fps             | 1115     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [148]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [149]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_71
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [150]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [151]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_72
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.4     |
| time/              |          |
|    fps             | 1118     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [152]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [153]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_73
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.4     |
| time/              |          |
|    fps             | 1120     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [154]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [155]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_74
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -9.1     |
| time/              |          |
|    fps             | 1115     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [156]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [157]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_75
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.1     |
| time/              |          |
|    fps             | 1118     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [158]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [159]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_76
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.3     |
| time/              |          |
|    fps             | 1114     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [160]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [161]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_77
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.3     |
| time/              |          |
|    fps             | 1101     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [162]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [163]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_78
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.4     |
| time/              |          |
|    fps             | 1117     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [164]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [165]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_79
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -7.8     |
| time/              |          |
|    fps             | 1118     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [166]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [167]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_80
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -7.9     |
| time/              |          |
|    fps             | 1100     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [168]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [169]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_81
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -7.8     |
| time/              |          |
|    fps             | 1118     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [170]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [171]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_82
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.1     |
| time/              |          |
|    fps             | 1119     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [172]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [173]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_83
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -7.7     |
| time/              |          |
|    fps             | 1105     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [174]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [175]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_84
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.5     |
| time/              |          |
|    fps             | 1103     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [176]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [177]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_85
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -7.8     |
| time/              |          |
|    fps             | 1106     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [178]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [179]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_86
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.8     |
| time/              |          |
|    fps             | 1093     |
|    iterati

In [180]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [181]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_87
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [182]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [183]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_88
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

In [184]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [185]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_89
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8.3     |
| time/              |          |
|    fps             | 1120     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [186]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [187]:
model.learn(total_timesteps=1000)

Logging to Test_Manual/PPO_90
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0,

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([

[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
[array([0, 0])]
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -8       |
| time/              |          |
|    fps             | 1100     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------


In [205]:
model.__dict__

{'policy_class': stable_baselines3.common.policies.ActorCriticPolicy,
 'device': device(type='cpu'),
 'env': <stable_baselines3.common.vec_env.dummy_vec_env.DummyVecEnv at 0x7f324df30970>,
 '_vec_normalize_env': None,
 'verbose': 1,
 'policy_kwargs': {},
 'observation_space': Box([-30   0   0   0   0], [30 30 30  1  1], (5,), int64),
 'action_space': MultiDiscrete([30 30]),
 'n_envs': 1,
 'num_timesteps': 2048,
 '_total_timesteps': 1000,
 '_num_timesteps_at_start': 0,
 'eval_env': None,
 'seed': None,
 'action_noise': None,
 'start_time': 1670578034336289209,
 'policy': ActorCriticPolicy(
   (features_extractor): FlattenExtractor(
     (flatten): Flatten(start_dim=1, end_dim=-1)
   )
   (mlp_extractor): MlpExtractor(
     (shared_net): Sequential()
     (policy_net): Sequential(
       (0): Linear(in_features=5, out_features=64, bias=True)
       (1): Tanh()
       (2): Linear(in_features=64, out_features=64, bias=True)
       (3): Tanh()
     )
     (value_net): Sequential(
       (0)

In [188]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [189]:
model.predict(np.array([-6, 20, 15, 1, 1]))

(array([0, 0]), None)

In [190]:
model.predict(np.array([-100, 0, 80, 1, 1]))

(array([0, 0]), None)

In [191]:
model.predict(np.array([-100, 0, 0, 1, 1]))

(array([ 8, 18]), None)

In [192]:
model.predict(np.array([100, 0, 0, 1, 1]))

(array([0, 0]), None)

In [193]:
model.predict(np.array([100, 20, 35, 1, 1]))

(array([0, 0]), None)

In [194]:
model.predict(np.array([-100, 20, 35, 1, 1]))

(array([ 8, 26]), None)

In [195]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [196]:
model.predict(np.array([-100, 20, 35, 1, 1]))

(array([8, 3]), None)

In [197]:
model.predict(np.array([-30, 20, 35, 1, 1]))

(array([0, 0]), None)

In [198]:
model.predict(np.array([-30, 0, 0, 1, 1]))

(array([22, 19]), None)

In [199]:
model.predict(np.array([-30, 0, 0, 1, 1]))

(array([ 4, 12]), None)

In [200]:
model.predict(np.array([-30, 0, 0, 1, 1]))

(array([25, 12]), None)

In [201]:
model.predict(np.array([-30, 0, 0, 1, 1]))

(array([10, 14]), None)

In [202]:
model.predict(np.array([-30, 0, 0, 1, 1]))

(array([21, 14]), None)

In [206]:
model.predict(np.array([-6, 0, 0, 1, 1]))

(array([0, 0]), None)

In [207]:
model.predict(np.array([30, 0, 0, 1, 1]))

(array([0, 0]), None)